In [1]:
##Dependencies##
import folium 
import ee 
import geemap.foliumap as geemap
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point

##intialize and authenticate for google earth engine
#initialize ee
#ee.Authenticate() ##need to do once a week
ee.Initialize()

In [2]:
##Function to add ee layers from class##
def add_ee_layer(ee_layer, vis_param, map_object, layer_name, attribution="Google Earth Engine"):
    image = ee.Image(ee_layer).getMapId(vis_param)["tile_fetcher"].url_format #allos us to extract the tile's URL
    print(image) #print url for tile system
    folium.raster_layers.TileLayer(
        tiles= image,  # map url
        name= layer_name, #name of layer
        overlay=True, #stack layers
        control = True,  #adds interactive layer legend
        attr=attribution, #layer source

    ).add_to(map_object) # tells which map to add layer to

In [3]:
##Getting urban denisty raster image to create two different maps##
urban_density = ee.ImageCollection("JRC/GHSL/P2023A/GHS_BUILT_C").first()
SD_coords = [-117.35, 32.5, -116.8, 33]

##Filtering the data by a bounding box##
bbox_sd = ee.Geometry.Rectangle(SD_coords)
urban_density_sd = urban_density.clip((bbox_sd))


bbox_la = ee.Geometry.BBox(-118.9, 33.6, -117.6, 34.9)
urban_density_la = urban_density.clip((bbox_la))



In [16]:
tracts_df = gpd.read_file("/mnt/c/Users/tbrag/OneDrive/Desktop/bda602venv/tl_2019_06_tract/tl_2019_06_tract.shp")
tracts_gdf = gpd.GeoDataFrame(tracts_df, geometry='geometry')

SD_tract_clipped = tracts_gdf.clip(SD_coords)
# Bounding Box for the contiguous United States:
#bbox = Polygon([(-135, 24), (-135, 49.8), (-66.7, 49.8), (-66.7, 24)])

# Clip our GeoDataFrames & Give it a new Coordinate Reference System (CRS):
#states_clipped = states_df.clip(bbox).to_crs("EPSG:2163")

tracts_geojson = SD_tract_clipped.to_crs(epsg='4326').to_json()

In [4]:
##Adding SD DUI crash Data##
DUI_SD = pd.read_csv('/mnt/c/Users/tbrag/OneDrive/Desktop/bda602venv/SWITRS_SD_Alcohol.csv')

# Convert date column to datetime
DUI_SD['PROC_DATE'] = pd.to_datetime(DUI_SD['PROC_DATE'])

# Filter the DataFrame for crashes from 2017 or later
DUI_SD_filtered = DUI_SD[DUI_SD['PROC_DATE'].dt.year >= 2017]

# Create a geometry column with Point objects
DUI_SD_filtered['geometry'] = DUI_SD_filtered.apply(lambda row: Point(row.POINT_X, row.POINT_Y), axis=1)

# Create a GeoDataFrame from the DataFrame
DUI_SD_gdf = gpd.GeoDataFrame(DUI_SD_filtered, geometry='geometry')

# Filter out rows with empty geometries
DUI_SD_gdf_valid = DUI_SD_gdf[~DUI_SD_gdf.geometry.is_empty]

/tmp/ipykernel_393329/724019794.py:2: DtypeWarning: Columns (14) have mixed types. Specify dtype option on import or set low_memory=False.
  DUI_SD = pd.read_csv('/mnt/c/Users/tbrag/OneDrive/Desktop/bda602venv/SWITRS_SD_Alcohol.csv')
/tmp/ipykernel_393329/724019794.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  DUI_SD_filtered['geometry'] = DUI_SD_filtered.apply(lambda row: Point(row.POINT_X, row.POINT_Y), axis=1)


In [21]:
## Creating SD interactive map##
Map_SD = folium.Map(
    location = (32.7,-117.1),
    zoom_start = 11,
    tiles="http://mt0.google.com/vt/lyrs=y&hl=en&x={x}&y={y}&z={z}",
    attr="google satelite image",
    overlay=True,
    control = True
)
#Map_SD = geemap.Map(center=[32.7,-117.1], zoom=11)
#Map_SD.add_basemap("HYBRID")

##add ee layer of SD urban density
add_ee_layer(
    ee_layer = urban_density_sd,
    vis_param = {},
    map_object=Map_SD,
    layer_name = "Urban Density",
    )

##add dui crash point in boundingbox area##
for idx, row in DUI_SD_gdf_valid.iterrows():
    lat, lon = row.geometry.y, row.geometry.x
    # Check if the point is within the bounding box
    if SD_coords[1] <= lat <= SD_coords[3] and SD_coords[0] <= lon <= SD_coords[2]:
        folium.CircleMarker(
            location=[lat, lon],
            radius=3,  # Initial radius
            color='green',
            fill=True,
            fill_color='green',
            fill_opacity=1,
        ).add_to(Map_SD)

folium.GeoJson(
    tracts_geojson,
    name='Census Tracts',
).add_to(Map_SD)

Map_SD.save("map_image.html")

Map_SD

https://earthengine.googleapis.com/v1/projects/earthengine-legacy/maps/efc85761b0e74f43511d5b6dd41cd8ca-21496fbf2f4a9adcaaa2f7e86d51da86/tiles/{z}/{x}/{y}


In [6]:
## Creating LA interactive map##

Map_LA = geemap.Map(center=(34,-118.2), zoom=10.2)
Map_LA.add_basemap("HOpenStreetMap")

##add ee layer of SD urban density
add_ee_layer(
    ee_layer = urban_density_la,
    vis_param = {},
    map_object=Map_LA,
    layer_name = "Urban Density"
)
Map_LA


https://earthengine.googleapis.com/v1/projects/earthengine-legacy/maps/89919de21e06d0958775d40d829e686e-7d90f22b95e2d90639534a6dac603a01/tiles/{z}/{x}/{y}
